In [22]:
import h5py
import numpy as np
import matplotlib.pyplot as plt
import logging
from scipy.optimize import curve_fit
from argparse import ArgumentParser
import json
import os
import sys
from bokeh.plotting import figure, show
from bokeh.models import Span, Legend, LegendItem
from bokeh.io import output_notebook
import panel as pn
output_notebook()

Loading BokehJS ...

In [2]:
# Hutches that support jet tracking
HUTCHES = [
    'cxi',
    'mfx'
]

DETS = [
    'DsaCsPad',
    'DsbCsPad',
    'DscCsPad'
]

# The possible intensity monitors to use, prefer f_2.. since
# this is after the solid attenuators (maybe still true?)
# TODO: find wave8 key and add to I_MONS
I_MONS = [
    'f_11_ENRC',
    'f_12_ENRC',
    'f_21_ENRC',
    'f_22_ENRC',
    'f_63_ENRC',
    'f_64_ENRC'
]

# base path to experiment data
DATA_PATH = '/reg/d/psdm/'

# extension to small data hdf5 files
HDF5_EXT = '/hdf5/smalldata/'

# Calib directory to write results to
CAL_DIR = '/calib/'
CAL_FILE = 'jt_cal'

# dataset keys
GDET_KEY = 'gas_detector'
AZAV_KEY = 'azav_azav'

# Guassian Fitting
LINE_FIT_POINTS = 50
RADIAL_RANGE = 5

# Logger
f = '%(asctime)s - %(levelname)s - %(filename)s:%(funcName)s - %(message)s'
logging.basicConfig(level=logging.DEBUG, format=f)
logger = logging.getLogger(__name__)

In [3]:
# Math helper functions
def gaussian(x, a, mean, std, m, b):
    """Equation for gaussian with linear component/offset"""
    return (a * np.exp(-((x - mean) / 2 / std) ** 2)) + (m * x + b)

def fit_line(ave_azav, fit_points=LINE_FIT_POINTS):
    """Fit the line from edges of array"""
    azav_len = len(ave_azav)
    x0 = fit_points / 2
    x1 = azav_len - (fit_points / 2)
    y0 = np.mean(ave_azav[:fit_points])
    y1 = np.mean(ave_azav[azav_len - fit_points:])
    m, b = np.polyfit((x0, x1), (y0, y1), 1)

    return m, b

In [55]:
# Intensity monitor filter and plot

def calc_intensity_bounds(f, i_mon, low, hi):
    """Calculate lower and upper bounds to be used in jet tracking
    and generate indices of events to be used in calibration

    Parameters
    ----------
    f: h5py File Object
        The smalldata file to be analyzed
    i_mon: str
        The name of the intensity monitor we'll use
    low: float
        The number of sigmas below mean to include
    hi: float
        The number of sigmas above mean to include

    Returns
    -------
    i_low: float
        lower bound for intensity data
    i_hi: float
        upper bound for intensity data
    i_dat: np.ndarray
        The intensity data
    """
    # Set intensity monitor get data and set nan to 0.0
    if GDET_KEY not in f.keys():
        raise KeyError('Could not find intensity monitor key')

    logger.debug('Getting intensity data for {i_mon}')
    i_dat = np.array(f[GDET_KEY][i_mon])
    i_dat = np.nan_to_num(i_dat, copy=False)

    # Get upper and lower bounds
    mean = i_dat.mean()
    std = np.std(i_dat)

    i_low = round(mean - low * std, 2)
    i_hi = round(mean + hi * std, 2)
    logger.debug(f'Lower:Upper bounds for intensity monitor: {i_low}:{i_hi}')

    return i_dat, i_low, i_hi

def intensity_hist_median(i_dat, bins=100):
    """Generate the histogram and median for intensity data being used"""
    hist, edges = np.histogram(i_dat, bins=bins)
    median = np.median(i_dat)
    
    return hist, edges, median
    
def intensity_fig(i_mon, hist, edges, median):
        """Generate a histogram of intensity monitor data with bounds"""
        fig = figure(
            title=f'Used Intensity Distribution for {i_mon}. Low/Hi: {round(edges[0], 2)}/{round(edges[-1], 2)}.  Median: {round(median, 2)}',
            x_axis_label='Intensity Values',
            y_axis_label='Counts'
        )
        fig.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:])
        left_line = Span(location=edges[0], dimension='height', line_color='black')
        right_line = Span(location=edges[-1], dimension='height', line_color='black')
        median_line = Span(location=median, dimension='height', line_color='red')
        fig.renderers.extend([left_line, right_line, median_line])

        return fig

In [45]:
# Experiment and run to analyze, load hdf5 file
exp = 'cxilr6716'
run = '139'
hutch = exp[:3]
logger.debug(f'analyzing experiment {exp}, run number {run}')
exp_path = f'{DATA_PATH}{hutch}/{exp}'
sd_file = f'{exp_path}{HDF5_EXT}{exp}_Run{run}.h5'
f = h5py.File(sd_file, 'r')
logger.debug(f'loaded file with keys {f.keys()}')

2020-06-15 09:53:09,611 - DEBUG - <ipython-input-45-48682e281d89>:<module> - analyzing experiment cxilr6716, run number 139
2020-06-15 09:53:09,614 - DEBUG - <ipython-input-45-48682e281d89>:<module> - loaded file with keys <KeysViewHDF5 ['DsaCsPad', 'KbEncoder', 'UserDataCfg', 'damage', 'ebeam', 'epicsUser', 'event_time', 'evr', 'fiducials', 'gas_detector', 'lightStatus', 'phase_cav', 'scan']>


In [56]:
# Find upper and lower limits for intensity monitor
i_mon = 'f_21_ENRC'
i_dat , low, hi = calc_intensity_bounds(f, i_mon, 1.5, 1.5)

# Get indices of events we will use from calculated limits
idxs_use = np.where((i_dat >= low) & (i_dat <= hi))
i_dat = i_dat[idxs_use]

hist, edges, median = intensity_hist_median(i_dat)

# Plot results
show(intensity_fig(i_mon, hist, edges, median))

2020-06-15 10:01:29,403 - DEBUG - <ipython-input-55-a08db95e9693>:calc_intensity_bounds - Getting intensity data for {i_mon}
2020-06-15 10:01:29,409 - DEBUG - <ipython-input-55-a08db95e9693>:calc_intensity_bounds - Lower:Upper bounds for intensity monitor: 1.97:3.06


In [104]:
# Filter on azimuthally binned array
def det_azav(f, idxs_use):
    """Get the average azimuthally q binned array from used events"""
    # Find the detector term
    shared_det = set(DETS).intersection(f.keys())
    if not bool(shared_det):
        raise ValueError('smalldata file does not contain known detector')

    # Assuming they didn't have two different detector keys...
    det = shared_det.pop()
    logger.debug(f'Getting azimuthal values for detector: {det}')
    det_group = f[det]
    azav = np.array(det_group[AZAV_KEY])
    azav_use = azav[idxs_use]
    ave_azav = (azav_use.sum(axis=0) / len(azav_use))[0]
    logger.debug('Found azimuthal average arrays for all used events')

    return azav_use, ave_azav
    
def calc_peak_and_intensity(ave_azav, i_dat, median_intensity):
    """Fit the gaussian with linear offset and get the peak 
    and integrated intensity around peak
    """
    logger.debug('Fitting Guassian of average azimuthal binned array')
    azav_len = len(ave_azav)
    # Fit the line
    m, b = fit_line(ave_azav)

    # Estimate mean and std
    x = np.arange(azav_len)
    mean = sum(x * ave_azav) / sum(ave_azav)
    std = np.sqrt(sum((x - mean) ** 2 / azav_len))

    # Fit Gaussian and get center and integrated intensity
    popt, _ = curve_fit(gaussian, x, ave_azav, p0=[max(ave_azav), mean, std, m, b])
    peak = int(round(popt[1]))
    rad_start = peak - RADIAL_RANGE
    rad_end = peak + RADIAL_RANGE
    intensity = round(ave_azav[rad_start:rad_end].sum(axis=0) / median_intensity, 2)
    logger.debug(f'Peak found at {peak}, with and intensity of {intensity}') 

    return peak, intensity, rad_start, rad_end

def azav_fig(ave_azav, peak, intensity, rad_start, rad_end):
    """Generate the azav fig for html file"""
    x_vals = np.arange(len(ave_azav))
    fig = figure(
        title=f'Average Azimuthal Binned Array: Center - {peak}, min/max - {rad_start}/{rad_end}, intensity - {round(intensity, 2)}',
        x_axis_label='Bins',
        y_axis_label='Intensity',
    )

    peak_line = Span(location=peak, dimension='height', line_color='green', line_width=2)
    lower_line = Span(location=rad_start, dimension='height', line_color='black')
    upper_line = Span(location=rad_end, dimension='height', line_color='black')
    ave_azav_curve = fig.scatter(x_vals, ave_azav)
    fig.renderers.extend([peak_line, lower_line, upper_line])

    azav_legend = Legend(items=[
        LegendItem(label='Azimuthal Average', renderers=[ave_azav_curve])
    ])
    fig.add_layout(azav_legend)

    return fig

In [105]:
# Get all the azimuthally binned arrays to use and 
# the average array from all events
azav_use, ave_azav = det_azav(f, idxs_use)
peak, integrated_intensity, rad_start, rad_end = calc_peak_and_intensity(ave_azav, i_dat, median)
show(azav_fig(ave_azav, peak, intensity, rad_start, rad_end))

2020-06-15 12:19:56,545 - DEBUG - <ipython-input-104-2381c3b97b5b>:det_azav - Getting azimuthal values for detector: DsaCsPad
2020-06-15 12:19:57,805 - DEBUG - <ipython-input-104-2381c3b97b5b>:det_azav - Found azimuthal average arrays for all used events
2020-06-15 12:19:57,876 - DEBUG - <ipython-input-104-2381c3b97b5b>:calc_peak_and_intensity - Fitting Guassian of average azimuthal binned array
2020-06-15 12:19:57,891 - DEBUG - <ipython-input-104-2381c3b97b5b>:calc_peak_and_intensity - Peak found at 147, with and intensity of 235.07


In [106]:
# Get the peak (and min at some point) for each array
# Plot vs the intensity monitor value

def peak_in_bins(azav_use, peak, range=RADIAL_RANGE):
    """Get the peak in the bins we're using"""
    low = peak - RADIAL_RANGE
    hi = peak + RADIAL_RANGE
    peak_vals = [azav[0][peak] for azav in azav_use]

    return np.array(peak_vals)

def intensity_vs_peak_fig(intensity, peak_vals):
    """Simple plot of intensity vs peak value"""
    fig = figure(
        title='Peak value vs Intensity',
        x_axis_label='Intensity Monitor Value',
        y_axis_label='Peak Values'
    )
    fig.scatter(intensity, peak_vals)
    return fig

In [107]:
# Get the peak value for all azav arrays and plot vs intensity monitor value
peak_vals = peak_in_bins(azav_use, peak)
show(intensity_vs_peak_fig(i_dat, peak_vals))